# Import Library

In [1]:
import tweepy
import numpy as np
import pandas as pd
from tqdm import tqdm # untuk melihat progress
import pickle
import helper
from elang.word2vec.utils import cleansing
import re # untuk pencarian pola dalam teks

# Tulis API_key dan Access_token

In [2]:
api_key = "MjTJA1iwChIt5RM4DnqErDJsP"
api_key_secret = "0mCN6QnIwnpxHWDzoSLSgMjq1utpGRy7wKJ3iTw8ADG4gXWv2O"
access_token = "1305481934018023424-YrkEkL5FcawOThAnZcgxcaYZX1IWPs"
access_token_secret = "c5oSI8HcU7KcZSrKII8SAGzzEMm34abmFNlaTSxUiazjc"

# Lakukan AuthHandler

In [3]:
auth = tweepy.OAuthHandler(api_key, api_key_secret)
auth.set_access_token(access_token, access_token_secret)
api = tweepy.API(auth, wait_on_rate_limit=True, wait_on_rate_limit_notify=True, compression=True)

# Cari tweet berdasarkan hashtags #OmnibusLaw

In [4]:
kata_kunci = '#CabutOmnibusLaw since:2020-10-01 until:2020-12-10'
tweets = tweepy.Cursor(api.search,
                             q = kata_kunci,
                             tweet_mode = "extended",
                             ).items(1000)

tweets_list = [tweet for tweet in tqdm(tweets)]

255it [00:15, 16.89it/s]


# Kelompokkan user_mentions kedalam mentions, screen_name kedalam retweets dan mengelompokkan jenis tweet yang didapat apakah retweet atau mentions dan jumlah interaksi dengan orang lain

In [5]:
dari = []
ke = []
jenis = []
for sample in tweets_list:
    mentions = sample.entities['user_mentions']
    for mention in mentions:
        screen_name = mention['screen_name']
        tipe = "retweet" if hasattr(sample, 'retweeted_status') else "mentions"
        dari.append(sample.author.screen_name)
        ke.append(screen_name)
        jenis.append(tipe)

edges = pd.DataFrame([dari, ke, jenis], index=["from", "to", "type"]).T
edges['count'] = 1
edges = edges.groupby(["from", "to", "type"]).sum().reset_index()

# Simpan edges kedalam edges_baru.csv

In [6]:
edges.to_csv("edges_baru.csv", index=False)

# Baca file edges_baru.csv

In [7]:
pd.read_csv("edges_baru.csv")

from              to     type  count
0            10_igun  Muslim_AntiPKI  retweet      1
1       1MenujuDamai   QaillaAsyiqah  retweet      1
2           2ikhtiar   QaillaAsyiqah  retweet      1
3    30DetikTakHenti   QaillaAsyiqah  retweet      1
4           AJazuli5    JameelaNajma  retweet      1
..               ...             ...      ...    ...
209       ttaufik124     SaveMoslem1  retweet      1
210       ttaufik124       mathsoul1  retweet      1
211      ucokseparoh   QaillaAsyiqah  retweet      2
212        wahdinata     kanopimedia  retweet      1
213         wm_ade86   QaillaAsyiqah  retweet      1

[214 rows x 4 columns]

# Melihat hasil crawling tweets berdasarkan API

In [8]:
tweets_list

[Status(_api=<tweepy.api.API object at 0x0000014B2AAE6220>, _json={'created_at': 'Tue Dec 08 10:22:14 +0000 2020', 'id': 1336254753680986113, 'id_str': '1336254753680986113', 'full_text': 'RT @Dedemit_Medsos: Aku iri pada klian sahabat" ku \n\nDoakan kami agar bisa mati dalam khusnul khotimah \n\nمن اهل خير الى من اهل الجنة \n\nآمين…', 'truncated': False, 'display_text_range': [0, 140], 'entities': {'hashtags': [], 'symbols': [], 'user_mentions': [{'screen_name': 'Dedemit_Medsos', 'name': '#GanyangPKI', 'id': 1253036038986952704, 'id_str': '1253036038986952704', 'indices': [3, 18]}], 'urls': []}, 'metadata': {'iso_language_code': 'und', 'result_type': 'recent'}, 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1153967452385976322, 'id_str': '1153967452385976322', '

# Simpan kedalam file tweet yang disimpan kedalam data

In [9]:
with open('data/tweet', 'wb') as file:
    pickle.dump(tweets_list, file)

In [10]:
with open('data/tweet', 'rb') as file:
    tweets_list = pickle.load(file)

# Mengelompokkan berdasarkan hasil crawling kedalam dataframe yang terdiri dari mention, retweets, jenis text, teks yang telah dibersihkan dll

In [11]:
data = []
for tweet in tqdm(tweets_list):
    if(x:=tweet.entities['user_mentions']) != []:
        mentions = [user['screen_name'] for user in x]
    else:
        mentions = []
     
    if(x:=tweet.entities['hashtags']) != []:
        hashtags = [tag['text'] for tag in x]
    else:
        hashtags = []
    
    text = tweet.full_text
    id = tweet.id
    userid = tweet.author.id
    username = tweet.author.screen_name
    created_at = tweet.created_at
    likes = tweet.favorite_count # could be 0
    retweets = tweet.retweet_count
    isquote = tweet.is_quote_status
    is_retweet = True if hasattr(tweet, 'retweeted_status') else False 
    reply_to = tweet.in_reply_to_status_id # could be None
    geo = tweet.geo
    place = tweet.place
        
    data.append([text, id, userid, username, created_at, likes, retweets, isquote, is_retweet, mentions, hashtags, reply_to, geo, place])
hasiltweet = pd.DataFrame(data, columns=['text','id', 'userid', 'username', 'created_at', 'likes', 'retweets', 'isquote', 'is_retweet', 'mentions','hashtags','reply_to', 'geo', 'place' ])


100%|█████████████████████████████████████████████████████████████████████████████| 255/255 [00:00<00:00, 85250.08it/s]


# Melihat data top 5 data dari hasil crawling

In [12]:
hasiltweet.head()

text                   id  \
0  RT @Dedemit_Medsos: Aku iri pada klian sahabat...  1336254753680986113   
1  Aku iri pada klian sahabat" ku \n\nDoakan kami...  1336250488694726658   
2  RT @QaillaAsyiqah: Update ~ Di depan Gedung Ma...  1336238072116117505   
3  goks, australia berani melawan kapitalis demi ...  1336227153340366848   
4  #gagalkanomnibuslaw #cabutomnibuslaw #omnibusl...  1336224496756264960   

                userid         username          created_at  likes  retweets  \
0  1153967452385976322  budihar24541523 2020-12-08 10:22:14      0         1   
1  1253036038986952704   Dedemit_Medsos 2020-12-08 10:05:17      2         1   
2  1177403641449213952    FathoniJihada 2020-12-08 09:15:57      0        32   
3            227008861   levboyaburakab 2020-12-08 08:32:33      0         0   
4            227008861   levboyaburakab 2020-12-08 08:22:00      0         0   

   isquote  is_retweet          mentions  \
0    False        True  [Dedemit_Medsos]   
1    False       False                []   
2    False        True   [QaillaAsyiqah]   
3     True       False                []   
4     True       False                []   

                                            hashtags      reply_to   geo place  
0                                                 []           NaN  None  None  
1  [JagaUlama, cabutomnibuslaw, ganyangpki, oppos...  1.336250e+18  None  None  
2                                                 []           NaN  None  None  
3              [cabutomnibuslaw, gagalkanomnibuslaw]           NaN  None  None  
4  [gagalkanomnibuslaw, cabutomnibuslaw, omnibusl...           NaN  None  None

# Melakukan Process Preprocessing

In [13]:
def cleantext(teks):
    teks = teks.encode('ascii', 'ignore').decode('ascii') #menghilangkan emoji
    teks = cleansing.remove_stopwords_id(teks) # menghilangkan stopwords
    
    # Hilangakan tertawa 
    hehe_pattern = '(?:e{0,2}h{1,2}e{0,2}){2,}h?'
    
    #hilangkan link
    link_pattern = r'http\S+'
    
    #hilangkan tanda baca
    punct_pattern = r'[^\w\s]'
    
    teks = re.sub(f'{hehe_pattern, link_pattern}', '', teks) 
    
    teks = cleansing.remove_stopwords_id(teks)
    return teks

In [14]:
clean_text = []
for text in tqdm(hasiltweet['text']):
    clean_text.append(cleantext(text))
hasiltweet['text_clean'] = clean_text
# hasiltweet.to_csv('tweet_omnibuslaw.csv', index=False)

100%|████████████████████████████████████████████████████████████████████████████████| 255/255 [00:37<00:00,  6.88it/s]


In [15]:
hasiltweet.head()

text                   id  \
0  RT @Dedemit_Medsos: Aku iri pada klian sahabat...  1336254753680986113   
1  Aku iri pada klian sahabat" ku \n\nDoakan kami...  1336250488694726658   
2  RT @QaillaAsyiqah: Update ~ Di depan Gedung Ma...  1336238072116117505   
3  goks, australia berani melawan kapitalis demi ...  1336227153340366848   
4  #gagalkanomnibuslaw #cabutomnibuslaw #omnibusl...  1336224496756264960   

                userid         username          created_at  likes  retweets  \
0  1153967452385976322  budihar24541523 2020-12-08 10:22:14      0         1   
1  1253036038986952704   Dedemit_Medsos 2020-12-08 10:05:17      2         1   
2  1177403641449213952    FathoniJihada 2020-12-08 09:15:57      0        32   
3            227008861   levboyaburakab 2020-12-08 08:32:33      0         0   
4            227008861   levboyaburakab 2020-12-08 08:22:00      0         0   

   isquote  is_retweet          mentions  \
0    False        True  [Dedemit_Medsos]   
1    False       False                []   
2    False        True   [QaillaAsyiqah]   
3     True       False                []   
4     True       False                []   

                                            hashtags      reply_to   geo  \
0                                                 []           NaN  None   
1  [JagaUlama, cabutomnibuslaw, ganyangpki, oppos...  1.336250e+18  None   
2                                                 []           NaN  None   
3              [cabutomnibuslaw, gagalkanomnibuslaw]           NaN  None   
4  [gagalkanomnibuslaw, cabutomnibuslaw, omnibusl...           NaN  None   

  place                                         text_clean  
0  None  rt @dedemit_medsos: iri klian sahabat" ku doak...  
1  None  iri klian sahabat" ku doakan mati khusnul khot...  
2  None  rt @qaillaasyiqah: update ~ mahkamah konstitus...  
3  None  goks, australia berani melawan kapitalis keber...  
4  None  #gagalkanomnibuslaw #cabutomnibuslaw #omnibusl...